# PyMISP - An interactive tutorial: Basics

## Connecting to MISP
### Your configuration

In [ ]:
# The URL of the MISP instance to connect to
misp_url = 'http://127.0.0.1:9090/'
# Can be found in the MISP web interface under 
# http://+MISP_URL+/users/view/me -> Authkey
misp_key = 'btm3o1j6SzKUEsHiNz0vTMYzPfcc5eIKpfaWFADj'
# Should PyMISP verify the MISP certificate
misp_verifycert = False

In [ ]:
from pymisp import PyMISP

misp = PyMISP(misp_url, misp_key, misp_verifycert)

## Creating a MISP Event

### Directly

In [ ]:
event = misp.new_event(distribution=1,
               threat_level_id=1,
               analysis=1,
               info="Event from notebook")
print("Event id: %s" % event['Event']['id'])

### Using the MISPEvent constructor

In [ ]:
from pymisp import MISPEvent

event_obj = MISPEvent()
event_obj.distribution = 1
event_obj.threat_level_id = 1
event_obj.analysis = 1
event_obj.info = "Event from notebook 2"
event = misp.add_event(event_obj)
event_id = event['Event']['id']
print("Event id: %s" % event_id)

## Fetching a MISP Event

In [ ]:
# Fetch by ID
event = misp.get_event(event_id)
print(event)

## Adding Attribute to an event

### Adding directly

In [ ]:
attr_type = "ip-src"
value = "8.8.8.8"
category = "Network activity"
to_ids = False
proposal = False
updated_event = misp.add_named_attribute(event,
                                 attr_type,
                                 value,
                                 category=category,
                                 to_ids=to_ids,
                                 proposal=proposal)
print(updated_event)

### Using the MISPAttribute constructor

In [ ]:
from pymisp import MISPAttribute

# Attribute data already defined
attribute = MISPAttribute()
attribute.type = attr_type
attribute.value = value
attribute.category = category
attribute.proposal = proposal
print(attribute)

In [ ]:
# An attribute can also be loaded directly from a JSON
json = '''{
    "type": "ip-dst",
    "value": "127.0.0.1",
    "category": "Network activity",
    "to_ids": false,
    "proposal": false
    }'''

attribute = MISPAttribute()
attribute.from_json(json)
print(attribute)

### And then, update the event

In [ ]:
# Add the attribute to the event
## Fetch the event from MISP
event_dict = misp.get(event_id)['Event']

## Convert it to a PyMISP Event
event = MISPEvent()
event.from_dict(**event_dict)
## Let MISP update the timestamp. Otherwise, MISP will compare the two timestamps 
## (which are equals) and reject the the update
del event.timestamp

## Add the attribute to the event
event.attributes.append(attribute)

## Push the updated event to MISP
event_dict = misp.update(event)
print(event_dict)

## Performing search

### Events by their info fields

In [ ]:
results = misp.search_index(eventinfo='notebook')
# The data is stored in the field 'response'
results = results['response']

for event in results:
    print(event['id'], ':', event['info'])

### Attributes by their values

### Search in all attributes

In [ ]:
# Search attributes (specified in controller) where the attribute type is 'ip-src'
# And the to_ids flag is set
response = misp.search(controller='attributes', type_attribute='ip-src', to_ids=False)
# The data is stored in the field 'response'
results = response['response']

# Get all related event
attributes = results['Attribute']
event_ids = set()
for attr in attributes:
    event_ids.add(event_id)

# Fetch all related events
for event_id in event_ids:
    event = misp.get_event(event_id)
    print(event['Event']['info'])

## Creating and adding a MISP Object

In [ ]:
from pymisp import MISPObject

object_name = 'email'
object_data = {
    'from': 'admin@admin.test',
    'to': 'admin@foo.bar',
    'subject': 'An email',
}

# Retreive the template ID from the object's name
## Fetch all templates
templates = misp.get_object_templates_list()
## Get the template matching with the object's name
template_id = None
for template in templates:
    cur_name = template['ObjectTemplate']['name']
    cur_id = template['ObjectTemplate']['id']
    if cur_name == object_name:
        template_id = cur_id
        break    
if template_id is None:
    raise Exception('No matching template')

# Create the MISP Object
misp_obj = MISPObject(object_name)
for obj_relation, value in object_data.items():
    misp_obj.add_attribute(obj_relation, **{'value': value})

# Add the object to MISP
response = misp.add_object(event_id,
                           template_id,
                           misp_obj)
print(response)